# Homework 16


In [1]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from scipy.integrate import quad
from scipy.interpolate import interp1d
from scipy.optimize import curve_fit, fsolve

### Problem 1
Use fsolve to find the two roots of the polynomial $f(x) = 2x^2 + 3x - 10$.

### Problem 2

Use fsolve to find the solution of the following two equations:

$$f(x,y) = 2x^{2/3}+y^{2/3}-9^{1/3},$$

$$g(x,y) = \frac{x^2}{4} + \sqrt{y} - 1. $$

Use an initial guess of $x_0=1$, $y_0$ = 1.

### Problem 3

Species heat capacities are given by:

$$c_{p,i}(T) = R_g(a_{0,i} + a_{1,i}T + a_{2,i}T^2 + a_{3,i}T^3 + a_{4,i}T^4).$$ 

| Species | $a_0$           | $a_1$             | $a_2$            | $a_3$             | $a_4$             |
|---------|-----------------|-------------------|------------------|-------------------|-------------------|
| 'CH4'| 1.28392437e+00|  1.00851346e-02| -2.66241814e-06|  4.99192762e-11|  5.62132385e-14|
| 'O2' | 2.92112373e+00|  2.25021636e-03| -1.33975172e-06|  3.97866288e-10| -4.37971416e-14|
| 'N2' | 3.30542104e+00|  3.63227936e-04|  5.26679110e-07| -3.30019712e-10|  5.24837849e-14|
| 'CO2'| 2.78249997e+00|  7.06457251e-03| -4.50912355e-06|  1.35740239e-09| -1.55514712e-13|
| 'H2O'| 3.80784936e+00|  3.17295233e-04|  1.41348052e-06| -6.61323323e-10|  8.91786378e-14|

**NOTE, THESE ARE NOT THE SAME AS IN PREVIOUS HOMEWORK.**

The enthalpy of the species at temperature $T$ is given by

$$h_i(T) = h_{f,i} + \int_{T_{ref}}^{T}c_{p,i}(T)dT.$$
* Here, $h_{f,i}$ is the heat of formation of the species at temperature $T_{ref}=298$. 

| Species | $h_{f,i}$ (J/mol)  |
|---------|--------------------|
| CO2     | -393509            |
| H2O(g)  | -241818            |
| O2      | 0                  |
| N2      | 0                  |
| CH4     | -74520             |

**Methane combustion is given by the following reaction**
$$CH_4 + 2O_2 + 7.52N_2 \rightarrow CO_2 + 2H_2O + 7.52N_2.$$
* The reactants are at room temperature (298 K).
* The products have the same enthalpy as the reactants, but are much hotter because internal energy in the chemical bonds has been converted to sensible energy.
* The product temperature is called the **adiabatic flame temperature**, and without heat losses is the temperature of a stoichiometric methane (~natural gas) flame.

**Find the adiabatic flame temperature in K and $^o$F** given by the following equation:

$$h_{CH4}(298) + 2h_{O2}(298) + 7.52h_{N_2}(298) = h_{CO2}(T_{ad}) + 2h_{H2O}(T_{ad}) + 7.52h_{N_2}(T_{ad}).$$

* This is one equation in one unknown.
* $h_{CH4}(298)$, etc., refers to the enthalpy of the species at a temperature of 298.


In [3]:
# Dictionaries of the data for convenience to save typing. 
# You can reuse or reformat (you don't have to use a dictionary).

a = {
     'CH4':np.array([1.28392437e+00,  1.00851346e-02, -2.66241814e-06,  4.99192762e-11,  5.62132385e-14]),
     'O2':np.array([2.92112373e+00,  2.25021636e-03, -1.33975172e-06,  3.97866288e-10, -4.37971416e-14]),
     'N2':np.array([3.30542104e+00,  3.63227936e-04,  5.26679110e-07, -3.30019712e-10,  5.24837849e-14]),
     'CO2':np.array([2.78249997e+00,  7.06457251e-03, -4.50912355e-06,  1.35740239e-09, -1.55514712e-13]),
     'H2O':np.array([3.80784936e+00,  3.17295233e-04,  1.41348052e-06, -6.61323323e-10,  8.91786378e-14]),
    }

hf = {
      'CO2': -393509,
      'H2O': -241818,
      'O2' : 0,
      'N2' : 0,
      'CH4': -74520,
     }

#------------------------




### Problem 4 

We have a parallel pipe network with three pips. We want to find the flow rates $Q$ through each pipe. The flow rates are written in terms of the friction factors $f$ for each pipe.

We have the following unknowns $Q_0$, $Q_1$, $Q_2$, $f_0$, $f_1$, $f_2$. 

We have the following six equations in these unknowns:

$$Q_0 + Q_1 + Q_2 = Q_{tot},$$

$$\frac{f_0L_0\rho}{2D_0}\left(\frac{4Q_0}{\pi D_0^2}\right)^2 = \frac{f_1L_1\rho}{2D_1}\left(\frac{4Q_1}{\pi D_1^2}\right)^2,$$

$$\frac{f_0L_0\rho}{2D_0}\left(\frac{4Q_0}{\pi D_0^2}\right)^2 = \frac{f_2L_2\rho}{2D_2}\left(\frac{4Q_2}{\pi D_2^2}\right)^2,$$

$$\frac{1}{\sqrt{f_0}} = -2\log_{10}\left(\frac{\epsilon_0}{3.7D_0} + \frac{2.51\mu\pi D_0}{4\rho Q_0\sqrt{f_0}}\right),$$

$$\frac{1}{\sqrt{f_1}} = -2\log_{10}\left(\frac{\epsilon_1}{3.7D_1} + \frac{2.51\mu\pi D_1}{4\rho Q_1\sqrt{f_1}}\right),$$
 
$$\frac{1}{\sqrt{f_2}} = -2\log_{10}\left(\frac{\epsilon_2}{3.7D_2} + \frac{2.51\mu\pi D_2}{4\rho Q_2\sqrt{f_2}}\right).$$

The following quantities are given:

$$Q_{tot} = 0.01333\,m^3/s,$$
$$L_0 = 100\,{m},$$
$$L_1 = 150\,{m},$$
$$L_2 = 80\,{m},$$
$$D_0 = 0.05\,{m},$$
$$D_1 = 0.045\,{m},$$
$$D_2 = 0.04\,{m},$$
$$\epsilon_0 = 0.00024\,{m},$$
$$\epsilon_1 = 0.00012\,{m},$$
$$\epsilon_2 = 0.0002\,{m},$$
$$\mu = 1.002\times 10^{-3}\,kg/(m\cdot s),$$
$$\rho = 998\,kg/m^3.$$

It is a good idea to make your guesses consistent. That, make sure your guesses for $Q_0$, $Q_1$, and $Q_2$ add up to the given $Q_{tot}$. Reasonable guesses for $f_0$, $f_1$, $f_2$ are 0.01. 

Notes: 
* The first equation says the total flow rate is the sum of the flow rates through each pipe. 
* The second equation says that the pressure drop through pipe 0 is the same as that through pipe 1, since pipes 0 and 1 are connected at their ends.
* The third equation says that the pressure drop through pipe 1 is the same as that through pipe 2, since pipes 1 and 2 are connected at their ends.
* The last three equations relate the friction factor in each pipe to its flow rate and pipe properties.
* In the second two equations, $4Q/(\pi D^2)$ is just the velocity in the pipe. But we substituted $v=4Q/(\pi D^2)$ for convenience even though it makes the equations a bit harder to read. An alternative would be to define local terms like $v_0 = 4Q_0/(\pi D_0^2)$, and then use $v_0$ in the equations above instead of $4Q_0/(\pi D_0^2)$.
* In the frictions factor equations, $\mu\pi D/(4\rho Q)$ is just $1/Re$. Again, we made the substitution for convenience, but again, we could have written local variables for the $Re$'s and then used the $Re$'s in the equations.